  # Neural Network Training for the actuarial approach

In [1]:
import numpy as np
import pandas as pd
from scipy.optimize import fsolve
import matplotlib.pyplot as plt 

plt.style.use('bmh')

import matplotlib
matplotlib.rcParams.update({'font.size': 16})

from tqdm import tqdm
%load_ext autoreload
%autoreload 2
%aimport IS_misc_functions
from IS_misc_functions import *
from misc_functions import *
from actuarial_training import *

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras import regularizers
from sklearn.preprocessing import MinMaxScaler, StandardScaler, RobustScaler, MaxAbsScaler,normalize
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
import json

### Create the neural network

In [2]:
def build_model(x,nr_neurons = 256,regul = 0.00):

    model = keras.Sequential([
        layers.Dense(nr_neurons,kernel_regularizer=regularizers.l2(regul),activation='relu',input_shape=[400]),
        layers.Dropout(0.2),
        layers.Dense(nr_neurons,kernel_regularizer=regularizers.l2(regul), activation='relu'),
        layers.Dropout(0.2),
        layers.Dense(nr_neurons,kernel_regularizer=regularizers.l2(regul), activation='relu'),
        layers.Dropout(0.2),
        layers.Dense(nr_neurons,kernel_regularizer=regularizers.l2(regul), activation='relu'),
        layers.Dropout(0.2),
        layers.Dense(1)
      ])
    opt1 = tf.keras.optimizers.Adam(learning_rate = 0.0005, beta_1=0.9, beta_2=0.999)
    model.compile(loss='mse',
                    optimizer=opt1,
                    metrics=['mae', 'mse'])
    scaler = StandardScaler().fit(x)
    return model, scaler

### Load the Training Data

In [3]:
# # Read Data
def read_data(xpath,ypath):
    df_x = pd.read_csv(xpath, header=None)
    df_x = df_x.dropna()
    df_x = df_x.iloc[:,1:]

    df_y = pd.read_csv(ypath, header=None)
    df_y = df_y.dropna()
    df_y = df_y.iloc[:,1:]
    
    return df_x,df_y
x,y = read_data("csv/X_1.csv","csv/Y_1.csv")
for i in range(2,11):
    x_new,y_new = read_data("csv/X_"+str(i)+".csv","csv/Y_"+str(i)+".csv")
    x = pd.concat([x,x_new])
    y = pd.concat([y,y_new])
x_train = x.reset_index(drop = True)
y_train = y.reset_index(drop = True)

x_test, y_test = read_data("csv/X_test.csv","csv/Y_test.csv")



# Compute GA approx on the training set and test set

In [4]:
# Training set
GA_approx_List_Train = []
GA_approx_List_Test = []
for i in range(len(x_train)):
 
    LGD_Vector = x_train.iloc[i,:100]
    EAD_Vector = x_train.iloc[i,100:200]
    PD_Vector = x_train.iloc[i,200:300]
    omega_vector = x_train.iloc[i,300:]
    GA_approx_List_Train.append(GA_GL(PD_Vector[PD_Vector>0],
                              LGD_Vector[LGD_Vector>0],
                              EAD_Vector[EAD_Vector>0], 1, # Vector of Maturities
      q = 0.999, # quantile level
      xi = 0.25, # precision parameter,
      nu = 0.25,# recovery parameter
      rho = omega_vector[omega_vector>0],
      LGD_constant = False)) 
# Test set
for i in range(len(x_test)):
    LGD_Vector = x_test.iloc[i,:100]
    EAD_Vector = x_test.iloc[i,100:200]
    PD_Vector = x_test.iloc[i,200:300]
    omega_vector = x_test.iloc[i,300:]
    GA_approx_List_Test.append(GA_GL(PD_Vector[PD_Vector>0],
                              LGD_Vector[LGD_Vector>0],
                              EAD_Vector[EAD_Vector>0], 1, # Vector of Maturities
      q = 0.999, # quantile level
      xi = 0.25, # precision parameter,
      nu = 0.25,# recovery parameter
      rho = omega_vector[omega_vector>0],
      LGD_constant = False)) 
    
pd.DataFrame(GA_approx_List_Train).to_csv("csv/X_Train_act_approx.csv")
pd.DataFrame(GA_approx_List_Test).to_csv("csv/X_Test_act_approx.csv")

C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as me

C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as me

C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_c

C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as me

C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_c

...

C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_c

C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_c

C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as me

C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as me

C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_corr))*norm.ppf(PD)+np.sqrt(R_corr/(1-R_corr))*norm.ppf(q))-PD*ELGD)*(1/(1-1.5*b))*(1+(M-2.5)*b)
C:\Users\julia\anaconda3\lib\site-packages\scipy\optimize\minpack.py:175: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
C:\Users\julia\OneDrive - National University of Singapore\Projects\Capital Requirements of MDBs\Code_new\misc_functions.py:130: RuntimeWarning: invalid value encountered in sqrt
  K = ((ELGD)*norm.cdf(np.sqrt(1/(1-R_c